<font size = "5">

Import packages

In [3]:
import requests      # Requests data from an API
import jmespath      # Allows you to mor easily navigate JSON objects
import pandas as pd  # Handles data frames

import json          # Handles JSON object


<font size = "5">

Question 1

In [2]:

# check if the url works 
url_openalex_api = \
      "https://api.openalex.org/works?filter=title.search:artificial%20intelligence "

In [3]:
#more formally, use params function to filter

url_openalex_api = f"https://api.openalex.org/works"


params = {
    'filter': f'title.search:artificial intelligence',
}

search_results = requests.get(url_openalex_api,params=params)

num_papers = search_results.json()['meta']['count']


#summarize result
print(f"There are {num_papers} papers that mention artificial intelligence in title")

There are 139562 papers that mention artificial intelligence in title


In [4]:

# Obtain the JSON data of records from the open alex API


all_results = requests.get(url_openalex_api).json()

#visualize documents 


with open('json_files/convert_search_results.json', 'w') as file: 
    file.write(json.dumps(all_results, indent =4))


<font size = "5">

Question 2

In [6]:
# url with a placeholder for cursor
url_with_cursor = 'https://api.openalex.org/works?filter=title.search:artificial%20intelligence&filter=from_publication_date:2020-01-01&cursor={}'

cursor = '*'



# collect the data in a variable called `AI_work`.
# Initialize this as an empty list, which we will append to
AI_work = []


# loop through pages
while cursor:
    
    # set cursor value and request page from OpenAlex
    url = url_with_cursor.format(cursor)
    print("\n" + url)
    page_with_results = requests.get(url).json()

 
    
    # loop through partial list of results
    results = page_with_results['results']
    for api_result in results:
        AI_work.append(api_result)

    # update cursor to meta.next_cursor
    cursor = page_with_results['meta']['next_cursor']


https://api.openalex.org/works?filter=title.search:artificial%20intelligence&filter=from_publication_date:2020-01-01&cursor=*

https://api.openalex.org/works?filter=title.search:artificial%20intelligence&filter=from_publication_date:2020-01-01&cursor=IlsyMzg5LjI2MDcsIDE1NTkzNDcyMDAwMDAsICdodHRwczovL29wZW5hbGV4Lm9yZy9XMjk1MzUzMjg3NSddIg==

https://api.openalex.org/works?filter=title.search:artificial%20intelligence&filter=from_publication_date:2020-01-01&cursor=IlsxODEyLjY2MTUsIDE1MTg2NTI4MDAwMDAsICdodHRwczovL29wZW5hbGV4Lm9yZy9XMjc5MTY5NDA1MSddIg==

https://api.openalex.org/works?filter=title.search:artificial%20intelligence&filter=from_publication_date:2020-01-01&cursor=IlsxNTMwLjIwNCwgNTk5NjE2MDAwMDAwLCAnaHR0cHM6Ly9vcGVuYWxleC5vcmcvVzIxNzExNDQ3NjcnXSI=

https://api.openalex.org/works?filter=title.search:artificial%20intelligence&filter=from_publication_date:2020-01-01&cursor=IlsxMzk5LjYyNzksIDEyODc1MzI4MDAwMDAsICdodHRwczovL29wZW5hbGV4Lm9yZy9XMTk5ODM5OTU3MSddIg==

https://api.openalex

In [10]:
# Put the data for `counts_by_year` into a Pandas dataframe.
data1 = []
for work in AI_work:
    for authorships in work['authorships']:
        data1.append({
            'id': work['id'],
            'year': work['publication_year'],
            'country': authorships[0]['countries'],
          
            'author': authorships['author']['display_name'],
            'affiliation': authorships['institution']['display_name'],
            'cited_by_count': int(work['cited_by_count']),
        })
df_counts = pd.DataFrame(data1)

# Each row in the dataframe represents one year of one source.
# We can group by year and sum the number of works to get the
# total counts by year.

KeyError: 0

In [7]:
# Define the fields that we are interested in collecting:
fields = [
    'id',
    'title',
    'publication_year',
    'authorships',
    'cited_by_count',
    'type',
]

# One way to limit the dataframe to include only our `fields` is to use the `from_records()` method
# and specify only the columns we want.


df_works = pd.DataFrame.from_records(AI_work, columns=fields)


nested_df = pd.DataFrame(df_works['authorships'].tolist(), index=df_works.index)[0]


In [12]:
nested = df_works['authorships'].tolist()


[[{'author_position': 'first',
   'author': {'id': 'https://openalex.org/A5007305440',
    'display_name': 'Stuart Russell',
    'orcid': 'https://orcid.org/0000-0001-5252-4306'},
   'institutions': [{'id': 'https://openalex.org/I95457486',
     'display_name': 'University of California, Berkeley',
     'ror': 'https://ror.org/01an7q238',
     'country_code': 'US',
     'type': 'education',
     'lineage': ['https://openalex.org/I95457486']}],
   'countries': ['US'],
   'is_corresponding': False,
   'raw_author_name': 'Stuart J. Russell',
   'raw_affiliation_strings': ['University of California, Berkeley'],
   'affiliations': [{'raw_affiliation_string': 'University of California, Berkeley',
     'institution_ids': ['https://openalex.org/I95457486']}]},
  {'author_position': 'last',
   'author': {'id': 'https://openalex.org/A5080389385',
    'display_name': 'Peter Norvig',
    'orcid': None},
   'institutions': [{'id': 'https://openalex.org/I1174212',
     'display_name': 'University of

In [33]:
url_country = \
      "https://api.openalex.org/works?page=1&filter=display_name.search%3Aartificial%20intelligence,publication_year%3A2020-2024&group_by=authorships.countries"


country_results = requests.get(url_country).json()


with open('json_files/convert_country_results.json', 'w') as file: 
    file.write(json.dumps(country_results, indent =4))



In [36]:


result = country_results["meta"]

country_number = result["groups_count"]

print(country_number)

country_data = pd.DataFrame([])

for i in range(0,country_number):
    individual_data =country_results["group_by"][i]
    country_data.loc[i,1] = individual_data["key_display_name"]
    country_data.loc[i,2] = individual_data["count"]



196


<font size = "5">

Question 4

In [58]:
data_keyword= ["Artificial Intelligence", "LLM", "GPT", "Machine Learning"]

df_keyword= pd.DataFrame(data_keyword, columns=['words'])

keywords = ["Artificial Intelligence", "LLM", "GPT","Machine Learning"]
keywords[2]

'GPT'

In [60]:
df_compare = pd.DataFrame([])

for i in range(0, 4):
 keyword = keywords[i]
  for j in range(0,25):
       year = 2000 + j
       url = "https://api.openalex.org/works"
       params = {'filter': f'display_name.search:{keyword},publication_year:{year}'
}
       r= requests.get(url, params=params)
       num_works = r.json()['meta']['count']
       df_compare.loc[j,i] = num_works

IndentationError: unexpected indent (198057412.py, line 5)

In [62]:
df_compare = pd.DataFrame([])

for i in range(0,4): 
    keyword = keywords[i]
    for j in range(0,25):
        year= 2000 + j 
        url = "https://api.openalex.org/works"
        params = {'filter':f'display_name.search:{keyword}, publication_year:{year}'}
        r= requests.get(url, params=params)
        num_works = r.json()['meta']['count']
        df_compare.loc[j,i] = num_works

        

KeyError: 'meta'